# Julia Basics & VAR Process

Business Cycles and Fluctuations - AE2E6

> **Objectives**
>
> -   Introduce Julia environment
>     -   run cells
>     -   basic types: numbers, strings, vectors, matrices
>     -   functions
>     -   simple plots
> -   Simulate AR1 models
>     -   impulse response functions
>     -   stochastic simulations
>         -   conditional / unconditional moments
>     -   develop intuition about eigenvalues / ergodic distributions

# Julia: Quick Introduction

## Why Julia?

Developped at MIT on top of **opensource** technologies

-   linux / git / llvm

Syntax inspired by Matlab but:

-   more consistent
-   lots of features from high level languages

Everything is JIT-compiled

-   no interpreted vs compiled treadeoff -\> very fast
-   most of the base library is written in Julia

Opensource/free + vibrant community

## Numbers

In [65]:
# numbers (usual operations usual)
(1.0+(2.0+3.0*(4.0+5.0)))/30

1.0

In [66]:
# exponentials are denoted by ^
2^8

256

## Variables / assignments / comparisons

In [67]:
# variable assignment
x = 10

10

In [68]:
# Variable names can have Unicode characters
# To get ϵ in the REPL, type \epsilon<TAB>
a = 20
σ = 34
ϵ = 1e-4

0.0001

In [69]:
# comparison 
2 == 3

false

In [70]:
3<=3

true

## Strings

In [71]:
# Strings can also contain Unicode characters
fancy_str = "α is a string"

"α is a string"

In [72]:
# double quotes define a character, not a string
'c' 

'c': ASCII/Unicode U+0063 (category Ll: Letter, lowercase)

In [73]:
# string interpolation (1/2)
he_who_must_not_be_named = "Voldemort"
"Welcome $(he_who_must_not_be_named)!"

"Welcome Voldemort!"

In [74]:
# string interpolation (2/2)
n = 1999999
println("Iteration ", n, " is still running...")

Iteration 1999999 is still running...

## Arrays

In [75]:
# vectors
v = [1,2,3]

3-element Vector{Int64}:
 1
 2
 3

In [76]:
# matrices 
M = [1 2 3 ; 4 5 6 ; 7 8 9]

3×3 Matrix{Int64}:
 1  2  3
 4  5  6
 7  8  9

In [77]:
# matrix multiplication
M*v

3-element Vector{Int64}:
 14
 32
 50

In [78]:
# mutating vectors
x = ["One"]
push!(x, "Two")
push!(x, "Three")
push!(x, "Four")
push!(x, "Five")

# Note how the type of the vector is different from above
# Vectors in Julia hold homoegenous types

# Also note the exclation mark in `push!`: it is a reminder
# of the fact that `push!` mutates its first argument

5-element Vector{String}:
 "One"
 "Two"
 "Three"
 "Four"
 "Five"

In [79]:
# access elements in a vector
v[1]

1

In [80]:
# access elements in a matrix
M[1,2]

2

> **Warning**
>
> Indexing in Julia is 1-based. First element of a collection is denoted
> by 1.

In [81]:
# slice matrices
println(M)

# keep first line
println("First line")
println(M[1,:])

# keep second column
println("Second column")
println(M[:,2])

# extract a submatrix
println(M[1:2,1:2])

[1 2 3; 4 5 6; 7 8 9]
First line
[1, 2, 3]
Second column
[2, 5, 8]
[1 2; 4 5]

In [82]:
# concatenate vectors (horizontally)
vcat( [1,2], [3,4])

4-element Vector{Int64}:
 1
 2
 3
 4

In [83]:
# concatenate vectors
hcat( [1,2], [3,4])

2×2 Matrix{Int64}:
 1  3
 2  4

In [84]:
# transpose matrix
hcat( [1,2], [3,4])'

2×2 adjoint(::Matrix{Int64}) with eltype Int64:
 1  2
 3  4

## Tuples

In [85]:
# like in python
# tuples can hold heterogenous data
t = ("This", "is", 1, "tuple")

("This", "is", 1, "tuple")

In [86]:
# access elements in a tuple (still 1-based)
t[3]

1

In [87]:
# tuples are `immutable`
# The following should raise an exception
push!(t, "not a vector")

## Loops

In [88]:
# loop over any iterable (like in python)
for i in 1:5
    println("Iteration ", i)
end
# note how 1 and 5 are both included.


Iteration 1
Iteration 2
Iteration 3
Iteration 4
Iteration 5

In [89]:
for i ∈ ["Paris", "New-York", "Bogota"]
    println("City: ", i)
end

City: Paris
City: New-York
City: Bogota

In [90]:
# Vector comprehensions (like in python)
# enumerate all squares of even numbers (% computes modulo)
[i^2 for i=1:10 if i%2==1]

5-element Vector{Int64}:
  1
  9
 25
 49
 81

## Functions

In [91]:
# matlab like syntax
# with positional and keyword arguments separated by `;`

function fun(a,b; c=3)
    z = a+b*c
    return z
end

fun (generic function with 1 method)

In [92]:
fun(1,2)

7

In [93]:
fun(1,2; c=4)

9

# Manipulating AR1 Models

We consider here a simple autoregressive model:

$$y_t = A y_{t-1} + B e_t$$

where $y_t=(y^1_t, y^2_t)$ a vector of variables and
$e_t=(e^1_t, e^2_t)$ a normal i.i.d. multivariate process defined by
covariance matrix $\Sigma \in R^p \times R^p$.

We start by choosing:

$$A = \begin{bmatrix}\rho & 2 \\ 0 & \lambda\end{bmatrix}$$

$$B = \begin{bmatrix}1 & 0 \\ 0 & 1\end{bmatrix}$$

$$\Sigma = \begin{bmatrix}0.05 & 0.005 \\ 0.005 & 0.01\end{bmatrix}$$

**Define julia variables for matrices $A, B, \Sigma$.**

In [94]:
ρ = 0.3
λ = 0.5
A = [ρ 2; 0 λ]

2×2 Matrix{Float64}:
 0.3  2.0
 0.0  0.5

In [95]:
# B is the identity matrix
B = [1.0 0.0; 0.0 1.0] # pay attention to use floats rather than integers

2×2 Matrix{Float64}:
 1.0  0.0
 0.0  1.0

In [96]:
# a more julian way of using the identity matrix
using LinearAlgebra: I
B = I
# the resulting object adapts to any size (no need to instantiate it)

UniformScaling{Bool}
true*I

In [97]:
Σ = [0.05 0.005; 0.005 0.01]

2×2 Matrix{Float64}:
 0.05   0.005
 0.005  0.01

**Compute (programmatically) the eigenvalues of A.**

In [98]:
using LinearAlgebra
eigvals(A)
# no surprise: these are equal to λ, ρ

2-element Vector{Float64}:
 0.3
 0.5

In [99]:
A*[0,1]

2-element Vector{Float64}:
 2.0
 0.5

**Simulate the response to a one deviation shock to $e^1_t$ and $e^2_t$
over 10 periods.**

In [100]:
# an easy to read / inefficient solution

# pay attention that diagonal terms in Σ contain the variance...

e0_1 = [sqrt(Σ[1,1]), 0.0]
e0_2 = [0.0, sqrt(Σ[2,2])]

sim_y_1 = hcat([A^n*e0_1 for n in 0:10]...)
sim_y_2 = hcat([ A^n*e0_2 for n in 0:10 ]...)

2×11 Matrix{Float64}:
 0.0  0.2   0.16   0.098   0.0544   0.02882   …  0.00193344   0.000970658
 0.1  0.05  0.025  0.0125  0.00625  0.003125     0.000195313  9.76563e-5

**Plot the result using Plots.jl**

In [101]:
using Plots

plot(sim_y_1[1,:])

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip170)" d="M446.627 1544.91 L462.947 1544.91 L462.947 1548.85 L441.002 1548.85 L441.002 1544.91 Q443.664 1542.16 448.248 1537.53 Q452.854 1532.88 454.035 1531.53 Q456.28 1529.01 457.16 1527.27 Q458.063 1525.51 458.063 1523.82 Q458.063 1521.07 456.118 1519.33 Q454.197 1517.6 451.095 1517.6 Q448.896 1517.6 446.442 1518.36 Q444.012 1519.13 441.234 1520.68 L441.234 1515.95 Q444.058 1514.82 446.512 1514.24 Q448.965 1513.66 451.002 1513.66 Q456.373 1513.66 459.567 1516.35 Q462.762 1519.03 462.762 1523.52 Q462.762 1525.65 461.951 1527.57 Q461.164 1529.47 459.058 1532.07 Q458.479 1532.74 455.377 1535.95 Q452.276 1539.15 446.627 1544.91 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip170)" d="M1269.92 1529.7 Q1266.77 1529.7 1264.92 1531.86 Q1263.09 1534.01 1263.09 1537.76 Q1263.09 1541.49 1264.92 1543.66 Q1266.77 1545.82 1269.92 1545.82 Q1273.07 1545.82 1274.9 1543.66 Q1276.75 1541.49 1276.75 1537.76 Q1276.75 1534.01 1274.9 1531.86 Q1273.07 1529.7 1269.92 1529.7 M1279.2 1515.05 L1279.2 1519.31 Q1277.44 1518.48 1275.64 1518.04 Q1273.86 1517.6 1272.1 1517.6 Q1267.47 1517.6 1265.01 1520.72 Q1262.58 1523.85 1262.23 1530.17 Q1263.6 1528.15 1265.66 1527.09 Q1267.72 1526 1270.2 1526 Q1275.41 1526 1278.42 1529.17 Q1281.45 1532.32 1281.45 1537.76 Q1281.45 1543.08 1278.3 1546.3 Q1275.15 1549.52 1269.92 1549.52 Q1263.92 1549.52 1260.75 1544.94 Q1257.58 1540.33 1257.58 1531.6 Q1257.58 1523.41 1261.47 1518.55 Q1265.36 1513.66 1271.91 1513.66 Q1273.67 1513.66 1275.45 1514.01 Q1277.26 1514.36 1279.2 1515.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip170)" d="M1678.29 1532.44 Q1674.95 1532.44 1673.03 1534.22 Q1671.13 1536 1671.13 1539.13 Q1671.13 1542.25 1673.03 1544.03 Q1674.95 1545.82 1678.29 1545.82 Q1681.62 1545.82 1683.54 1544.03 Q1685.46 1542.23 1685.46 1539.13 Q1685.46 1536 1683.54 1534.22 Q1681.64 1532.44 1678.29 1532.44 M1673.61 1530.45 Q1670.6 1529.7 1668.91 1527.64 Q1667.24 1525.58 1667.24 1522.62 Q1667.24 1518.48 1670.18 1516.07 Q1673.15 1513.66 1678.29 1513.66 Q1683.45 1513.66 1686.39 1516.07 Q1689.33 1518.48 1689.33 1522.62 Q1689.33 1525.58 1687.64 1527.64 Q1685.97 1529.7 1682.98 1530.45 Q1686.36 1531.23 1688.24 1533.52 Q1690.14 1535.82 1690.14 1539.13 Q1690.14 1544.15 1687.06 1546.83 Q1684 1549.52 1678.29 1549.52 Q1672.57 1549.52 1669.49 1546.83 Q1666.43 1544.15 1666.43 1539.13 Q1666.43 1535.82 1668.33 1533.52 Q1670.23 1531.23 1673.61 1530.45 M1671.9 1523.06 Q1671.9 1525.75 1673.56 1527.25 Q1675.25 1528.76 1678.29 1528.76 Q1681.29 1528.76 1682.98 1527.25 Q1684.7 1525.75 1684.7 1523.06 Q1684.7 1520.38 1682.98 1518.87 Q1681.29 1517.37 1678.29 1517.37 Q1675.25 1517.37 1673.56 1518.87 Q1671.9 1520.38 1671.9 1523.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip170)" d="M2101.09 1517.37 Q2097.48 1517.37 2095.65 1520.93 Q2093.85 1524.47 2093.85 1531.6 Q2093.85 1538.71 2095.65 1542.27 Q2097.48 1545.82 2101.09 1545.82 Q2104.73 1545.82 2106.53 1542.27 Q2108.36 1538.71 2108.36 1531.6 Q2108.36 1524.47 2106.53 1520.93 Q2104.73 1517.37 2101.09 1517.37 M2101.09 1513.66 Q2106.9 1513.66 2109.96 1518.27 Q2113.04 1522.85 2113.04 1531.6 Q2113.04 1540.33 2109.96 1544.94 Q2106.9 1549.52 2101.09 1549.52 Q2095.28 1549.52 2092.21 1544.94 Q2089.15 1540.33 2089.15 1531.6 Q2089.15 1522.85 2092.21 1518.27 Q2095.28 1513.66 2101.09 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> 
 
 
 
 
 
<path clip-path="url(#clip170)" d="M62.9365 1431.52 Q59.3254 1431.52 57.4967 1435.09 Q55.6912 1438.63 55.6912 1445.76 Q55.6912 1452.86 57.4967 1456.43 Q59.3254 1459.97 62.9365 1459.97 Q66.5707 1459.97 68.3763 1456.43 Q70.205 1452.86 70.205 1445.76 Q70.205 1438.63 68.3763 1435.09 Q66.5707 1431.52 62.9365 1431.52 M62.9365 1427.82 Q68.7467 1427.82 71.8022 1432.43 Q74.8809 1437.01 74.8809 1445.76 Q74.8809 1454.49 71.8022 1459.

In [102]:
# we can make to plots size by size
plot( plot(sim_y_1[1,:], title="\$y_1\$", legend=false), plot(sim_y_1[2,:], title="\$y_2\$", legend=false))

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip260)" d="M299.458 1544.91 L315.777 1544.91 L315.777 1548.85 L293.833 1548.85 L293.833 1544.91 Q296.495 1542.16 301.078 1537.53 Q305.684 1532.88 306.865 1531.53 Q309.11 1529.01 309.99 1527.27 Q310.893 1525.51 310.893 1523.82 Q310.893 1521.07 308.948 1519.33 Q307.027 1517.6 303.925 1517.6 Q301.726 1517.6 299.272 1518.36 Q296.842 1519.13 294.064 1520.68 L294.064 1515.95 Q296.888 1514.82 299.342 1514.24 Q301.796 1513.66 303.833 1513.66 Q309.203 1513.66 312.397 1516.35 Q315.592 1519.03 315.592 1523.52 Q315.592 1525.65 314.782 1527.57 Q313.995 1529.47 311.888 1532.07 Q311.309 1532.74 308.208 1535.95 Q305.106 1539.15 299.458 1544.91 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip260)" d="M669.92 1529.7 Q666.772 1529.7 664.92 1531.86 Q663.091 1534.01 663.091 1537.76 Q663.091 1541.49 664.92 1543.66 Q666.772 1545.82 669.92 1545.82 Q673.068 1545.82 674.897 1543.66 Q676.749 1541.49 676.749 1537.76 Q676.749 1534.01 674.897 1531.86 Q673.068 1529.7 669.92 1529.7 M679.202 1515.05 L679.202 1519.31 Q677.443 1518.48 675.638 1518.04 Q673.855 1517.6 672.096 1517.6 Q667.466 1517.6 665.013 1520.72 Q662.582 1523.85 662.235 1530.17 Q663.601 1528.15 665.661 1527.09 Q667.721 1526 670.198 1526 Q675.406 1526 678.415 1529.17 Q681.448 1532.32 681.448 1537.76 Q681.448 1543.08 678.3 1546.3 Q675.151 1549.52 669.92 1549.52 Q663.925 1549.52 660.753 1544.94 Q657.582 1540.33 657.582 1531.6 Q657.582 1523.41 661.471 1518.55 Q665.36 1513.66 671.911 1513.66 Q673.67 1513.66 675.452 1514.01 Q677.258 1514.36 679.202 1515.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip260)" d="M851.87 1532.44 Q848.537 1532.44 846.615 1534.22 Q844.717 1536 844.717 1539.13 Q844.717 1542.25 846.615 1544.03 Q848.537 1545.82 851.87 1545.82 Q855.203 1545.82 857.125 1544.03 Q859.046 1542.23 859.046 1539.13 Q859.046 1536 857.125 1534.22 Q855.226 1532.44 851.87 1532.44 M847.194 1530.45 Q844.185 1529.7 842.495 1527.64 Q840.828 1525.58 840.828 1522.62 Q840.828 1518.48 843.768 1516.07 Q846.731 1513.66 851.87 1513.66 Q857.032 1513.66 859.972 1516.07 Q862.912 1518.48 862.912 1522.62 Q862.912 1525.58 861.222 1527.64 Q859.555 1529.7 856.569 1530.45 Q859.949 1531.23 861.824 1533.52 Q863.722 1535.82 863.722 1539.13 Q863.722 1544.15 860.643 1546.83 Q857.588 1549.52 851.87 1549.52 Q846.152 1549.52 843.074 1546.83 Q840.018 1544.15 840.018 1539.13 Q840.018 1535.82 841.916 1533.52 Q843.815 1531.23 847.194 1530.45 M845.481 1523.06 Q845.481 1525.75 847.148 1527.25 Q848.838 1528.76 851.87 1528.76 Q854.879 1528.76 856.569 1527.25 Q858.282 1525.75 858.282 1523.06 Q858.282 1520.38 856.569 1518.87 Q854.879 1517.37 851.87 1517.37 Q848.838 1517.37 847.148 1518.87 Q845.481 1520.38 845.481 1523.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip260)" d="M1048.26 1517.37 Q1044.65 1517.37 1042.82 1520.93 Q1041.02 1524.47 1041.02 1531.6 Q1041.02 1538.71 1042.82 1542.27 Q1044.65 1545.82 1048.26 1545.82 Q1051.9 1545.82 1053.7 1542.27 Q1055.53 1538.71 1055.53 1531.6 Q1055.53 1524.47 1053.7 1520.93 Q1051.9 1517.37 1048.26 1517.37 M1048.26 1513.66 Q1054.07 1513.66 1057.13 1518.27 Q1060.21 1522.85 1060.21 1531.6 Q1060.21 1540.33 1057.13 1544.94 Q1054.07 1549.52 1048.26 1549.52 Q1042.45 1549.52 1039.38 1544.94 Q1036.32 1540.33 1036.32 1531.6 Q1036.32 1522.85 1039.38 1518.27 Q1042.45 1513.66 1048.26 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> 
 
 
 
 
 
<path clip-path="url(#clip260)" d="M62.9365 1433.68 Q59.3254 1433.68 57.4967 1437.24 Q55.6912 1440.79 55.6912 1447.92 Q55.6912 1455.02 57.4967 1458.59 Q59.3254 1462.13 62.9365 1462.13 Q66.5707 1462.13 68.3763 1458.59 Q70.205 1455.02 70.205 1447.92 Q70.205 1440.79 68.3763 1437.24 Q66.5707 1433.68 62.9365 1433.68 M62.9365 1429.98 Q68.7467 1429.98 71.8022 1434.58 Q74.8809 1439.17 74.8809 1447.92 Q74.8809 1456.64 71.8022 1461

In [103]:
# or maake two plots on the same graph:
pl = plot(  sim_y_1[1,:], label="\$e_1\$", title="\$y_1\$" )
plot!(pl,sim_y_1[2,:], label="\$e_2\$")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip350)" d="M446.627 1544.91 L462.947 1544.91 L462.947 1548.85 L441.002 1548.85 L441.002 1544.91 Q443.664 1542.16 448.248 1537.53 Q452.854 1532.88 454.035 1531.53 Q456.28 1529.01 457.16 1527.27 Q458.063 1525.51 458.063 1523.82 Q458.063 1521.07 456.118 1519.33 Q454.197 1517.6 451.095 1517.6 Q448.896 1517.6 446.442 1518.36 Q444.012 1519.13 441.234 1520.68 L441.234 1515.95 Q444.058 1514.82 446.512 1514.24 Q448.965 1513.66 451.002 1513.66 Q456.373 1513.66 459.567 1516.35 Q462.762 1519.03 462.762 1523.52 Q462.762 1525.65 461.951 1527.57 Q461.164 1529.47 459.058 1532.07 Q458.479 1532.74 455.377 1535.95 Q452.276 1539.15 446.627 1544.91 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip350)" d="M1269.92 1529.7 Q1266.77 1529.7 1264.92 1531.86 Q1263.09 1534.01 1263.09 1537.76 Q1263.09 1541.49 1264.92 1543.66 Q1266.77 1545.82 1269.92 1545.82 Q1273.07 1545.82 1274.9 1543.66 Q1276.75 1541.49 1276.75 1537.76 Q1276.75 1534.01 1274.9 1531.86 Q1273.07 1529.7 1269.92 1529.7 M1279.2 1515.05 L1279.2 1519.31 Q1277.44 1518.48 1275.64 1518.04 Q1273.86 1517.6 1272.1 1517.6 Q1267.47 1517.6 1265.01 1520.72 Q1262.58 1523.85 1262.23 1530.17 Q1263.6 1528.15 1265.66 1527.09 Q1267.72 1526 1270.2 1526 Q1275.41 1526 1278.42 1529.17 Q1281.45 1532.32 1281.45 1537.76 Q1281.45 1543.08 1278.3 1546.3 Q1275.15 1549.52 1269.92 1549.52 Q1263.92 1549.52 1260.75 1544.94 Q1257.58 1540.33 1257.58 1531.6 Q1257.58 1523.41 1261.47 1518.55 Q1265.36 1513.66 1271.91 1513.66 Q1273.67 1513.66 1275.45 1514.01 Q1277.26 1514.36 1279.2 1515.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip350)" d="M1678.29 1532.44 Q1674.95 1532.44 1673.03 1534.22 Q1671.13 1536 1671.13 1539.13 Q1671.13 1542.25 1673.03 1544.03 Q1674.95 1545.82 1678.29 1545.82 Q1681.62 1545.82 1683.54 1544.03 Q1685.46 1542.23 1685.46 1539.13 Q1685.46 1536 1683.54 1534.22 Q1681.64 1532.44 1678.29 1532.44 M1673.61 1530.45 Q1670.6 1529.7 1668.91 1527.64 Q1667.24 1525.58 1667.24 1522.62 Q1667.24 1518.48 1670.18 1516.07 Q1673.15 1513.66 1678.29 1513.66 Q1683.45 1513.66 1686.39 1516.07 Q1689.33 1518.48 1689.33 1522.62 Q1689.33 1525.58 1687.64 1527.64 Q1685.97 1529.7 1682.98 1530.45 Q1686.36 1531.23 1688.24 1533.52 Q1690.14 1535.82 1690.14 1539.13 Q1690.14 1544.15 1687.06 1546.83 Q1684 1549.52 1678.29 1549.52 Q1672.57 1549.52 1669.49 1546.83 Q1666.43 1544.15 1666.43 1539.13 Q1666.43 1535.82 1668.33 1533.52 Q1670.23 1531.23 1673.61 1530.45 M1671.9 1523.06 Q1671.9 1525.75 1673.56 1527.25 Q1675.25 1528.76 1678.29 1528.76 Q1681.29 1528.76 1682.98 1527.25 Q1684.7 1525.75 1684.7 1523.06 Q1684.7 1520.38 1682.98 1518.87 Q1681.29 1517.37 1678.29 1517.37 Q1675.25 1517.37 1673.56 1518.87 Q1671.9 1520.38 1671.9 1523.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip350)" d="M2101.09 1517.37 Q2097.48 1517.37 2095.65 1520.93 Q2093.85 1524.47 2093.85 1531.6 Q2093.85 1538.71 2095.65 1542.27 Q2097.48 1545.82 2101.09 1545.82 Q2104.73 1545.82 2106.53 1542.27 Q2108.36 1538.71 2108.36 1531.6 Q2108.36 1524.47 2106.53 1520.93 Q2104.73 1517.37 2101.09 1517.37 M2101.09 1513.66 Q2106.9 1513.66 2109.96 1518.27 Q2113.04 1522.85 2113.04 1531.6 Q2113.04 1540.33 2109.96 1544.94 Q2106.9 1549.52 2101.09 1549.52 Q2095.28 1549.52 2092.21 1544.94 Q2089.15 1540.33 2089.15 1531.6 Q2089.15 1522.85 2092.21 1518.27 Q2095.28 1513.66 2101.09 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> 
 
 
 
 
 
<path clip-path="url(#clip350)" d="M62.9365 1433.67 Q59.3254 1433.67 57.4967 1437.24 Q55.6912 1440.78 55.6912 1447.91 Q55.6912 1455.01 57.4967 1458.58 Q59.3254 1462.12 62.9365 1462.12 Q66.5707 1462.12 68.3763 1458.58 Q70.205 1455.01 70.205 1447.91 Q70.205 1440.78 68.3763 1437.24 Q66.5707 1433.67 62.9365 1433.67 M62.9365 1429.97 Q68.7467 1429.97 71.8022 1434.57 Q74.8809 1439.16 74.8809 1447.91 Q74.8809 1456.63 71.8022 1461.

In [104]:
# Let's combine everything

pl1 = plot(  sim_y_1[1,:], label="\$e_2\$", title="\$y_1\$" )
plot!(pl1,sim_y_1[2,:], label="\$e_2\$")
pl2 = plot(  sim_y_2[1,:], label="\$e_2\$", title="\$y_2\$" )
plot!(pl2,sim_y_2[2,:], label="\$e_2\$", legend=false)
plot(pl1, pl2)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip440)" d="M299.458 1544.91 L315.777 1544.91 L315.777 1548.85 L293.833 1548.85 L293.833 1544.91 Q296.495 1542.16 301.078 1537.53 Q305.684 1532.88 306.865 1531.53 Q309.11 1529.01 309.99 1527.27 Q310.893 1525.51 310.893 1523.82 Q310.893 1521.07 308.948 1519.33 Q307.027 1517.6 303.925 1517.6 Q301.726 1517.6 299.272 1518.36 Q296.842 1519.13 294.064 1520.68 L294.064 1515.95 Q296.888 1514.82 299.342 1514.24 Q301.796 1513.66 303.833 1513.66 Q309.203 1513.66 312.397 1516.35 Q315.592 1519.03 315.592 1523.52 Q315.592 1525.65 314.782 1527.57 Q313.995 1529.47 311.888 1532.07 Q311.309 1532.74 308.208 1535.95 Q305.106 1539.15 299.458 1544.91 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip440)" d="M669.92 1529.7 Q666.772 1529.7 664.92 1531.86 Q663.091 1534.01 663.091 1537.76 Q663.091 1541.49 664.92 1543.66 Q666.772 1545.82 669.92 1545.82 Q673.068 1545.82 674.897 1543.66 Q676.749 1541.49 676.749 1537.76 Q676.749 1534.01 674.897 1531.86 Q673.068 1529.7 669.92 1529.7 M679.202 1515.05 L679.202 1519.31 Q677.443 1518.48 675.638 1518.04 Q673.855 1517.6 672.096 1517.6 Q667.466 1517.6 665.013 1520.72 Q662.582 1523.85 662.235 1530.17 Q663.601 1528.15 665.661 1527.09 Q667.721 1526 670.198 1526 Q675.406 1526 678.415 1529.17 Q681.448 1532.32 681.448 1537.76 Q681.448 1543.08 678.3 1546.3 Q675.151 1549.52 669.92 1549.52 Q663.925 1549.52 660.753 1544.94 Q657.582 1540.33 657.582 1531.6 Q657.582 1523.41 661.471 1518.55 Q665.36 1513.66 671.911 1513.66 Q673.67 1513.66 675.452 1514.01 Q677.258 1514.36 679.202 1515.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip440)" d="M851.87 1532.44 Q848.537 1532.44 846.615 1534.22 Q844.717 1536 844.717 1539.13 Q844.717 1542.25 846.615 1544.03 Q848.537 1545.82 851.87 1545.82 Q855.203 1545.82 857.125 1544.03 Q859.046 1542.23 859.046 1539.13 Q859.046 1536 857.125 1534.22 Q855.226 1532.44 851.87 1532.44 M847.194 1530.45 Q844.185 1529.7 842.495 1527.64 Q840.828 1525.58 840.828 1522.62 Q840.828 1518.48 843.768 1516.07 Q846.731 1513.66 851.87 1513.66 Q857.032 1513.66 859.972 1516.07 Q862.912 1518.48 862.912 1522.62 Q862.912 1525.58 861.222 1527.64 Q859.555 1529.7 856.569 1530.45 Q859.949 1531.23 861.824 1533.52 Q863.722 1535.82 863.722 1539.13 Q863.722 1544.15 860.643 1546.83 Q857.588 1549.52 851.87 1549.52 Q846.152 1549.52 843.074 1546.83 Q840.018 1544.15 840.018 1539.13 Q840.018 1535.82 841.916 1533.52 Q843.815 1531.23 847.194 1530.45 M845.481 1523.06 Q845.481 1525.75 847.148 1527.25 Q848.838 1528.76 851.87 1528.76 Q854.879 1528.76 856.569 1527.25 Q858.282 1525.75 858.282 1523.06 Q858.282 1520.38 856.569 1518.87 Q854.879 1517.37 851.87 1517.37 Q848.838 1517.37 847.148 1518.87 Q845.481 1520.38 845.481 1523.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip440)" d="M1048.26 1517.37 Q1044.65 1517.37 1042.82 1520.93 Q1041.02 1524.47 1041.02 1531.6 Q1041.02 1538.71 1042.82 1542.27 Q1044.65 1545.82 1048.26 1545.82 Q1051.9 1545.82 1053.7 1542.27 Q1055.53 1538.71 1055.53 1531.6 Q1055.53 1524.47 1053.7 1520.93 Q1051.9 1517.37 1048.26 1517.37 M1048.26 1513.66 Q1054.07 1513.66 1057.13 1518.27 Q1060.21 1522.85 1060.21 1531.6 Q1060.21 1540.33 1057.13 1544.94 Q1054.07 1549.52 1048.26 1549.52 Q1042.45 1549.52 1039.38 1544.94 Q1036.32 1540.33 1036.32 1531.6 Q1036.32 1522.85 1039.38 1518.27 Q1042.45 1513.66 1048.26 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> 
 
 
 
 
 
<path clip-path="url(#clip440)" d="M62.9365 1433.67 Q59.3254 1433.67 57.4967 1437.24 Q55.6912 1440.78 55.6912 1447.91 Q55.6912 1455.01 57.4967 1458.58 Q59.3254 1462.12 62.9365 1462.12 Q66.5707 1462.12 68.3763 1458.58 Q70.205 1455.01 70.205 1447.91 Q70.205 1440.78 68.3763 1437.24 Q66.5707 1433.67 62.9365 1433.67 M62.9365 1429.97 Q68.7467 1429.97 71.8022 1434.57 Q74.8809 1439.16 74.8809 1447.91 Q74.8809 1456.63 71.8022 1461

Remarks: we see that the response to the second shock is not monotonous
(in the first two periods, $y_2$ increases). This is a result of the
fact that $|||A||| > \rho(A)$

**What do you get if one eigenvalue is equal to 1? Greater than 1?**

In [105]:
# unit root case
ρ = 0.3
λ = 1.0

A = [ρ 2; 0 λ]

e0_1 = [sqrt(Σ[1,1]), 0.0]
e0_2 = [0.0, sqrt(Σ[2,2])]

sim_y_1 = hcat([A^n*e0_1 for n in 0:10]...)
sim_y_2 = hcat([ A^n*e0_2 for n in 0:10 ]...)
pl1 = plot(  sim_y_1[1,:], label="\$e_1\$", title="\$y_1\$" )
plot!(pl1,sim_y_1[2,:], label="\$e_2\$")
pl2 = plot(  sim_y_2[1,:], label="\$e_1\$", title="\$y_2\$" )
plot!(pl2,sim_y_2[2,:], label="\$e_2\$", legend=false)
plot(pl1, pl2)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip530)" d="M299.458 1544.91 L315.777 1544.91 L315.777 1548.85 L293.833 1548.85 L293.833 1544.91 Q296.495 1542.16 301.078 1537.53 Q305.684 1532.88 306.865 1531.53 Q309.11 1529.01 309.99 1527.27 Q310.893 1525.51 310.893 1523.82 Q310.893 1521.07 308.948 1519.33 Q307.027 1517.6 303.925 1517.6 Q301.726 1517.6 299.272 1518.36 Q296.842 1519.13 294.064 1520.68 L294.064 1515.95 Q296.888 1514.82 299.342 1514.24 Q301.796 1513.66 303.833 1513.66 Q309.203 1513.66 312.397 1516.35 Q315.592 1519.03 315.592 1523.52 Q315.592 1525.65 314.782 1527.57 Q313.995 1529.47 311.888 1532.07 Q311.309 1532.74 308.208 1535.95 Q305.106 1539.15 299.458 1544.91 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip530)" d="M669.92 1529.7 Q666.772 1529.7 664.92 1531.86 Q663.091 1534.01 663.091 1537.76 Q663.091 1541.49 664.92 1543.66 Q666.772 1545.82 669.92 1545.82 Q673.068 1545.82 674.897 1543.66 Q676.749 1541.49 676.749 1537.76 Q676.749 1534.01 674.897 1531.86 Q673.068 1529.7 669.92 1529.7 M679.202 1515.05 L679.202 1519.31 Q677.443 1518.48 675.638 1518.04 Q673.855 1517.6 672.096 1517.6 Q667.466 1517.6 665.013 1520.72 Q662.582 1523.85 662.235 1530.17 Q663.601 1528.15 665.661 1527.09 Q667.721 1526 670.198 1526 Q675.406 1526 678.415 1529.17 Q681.448 1532.32 681.448 1537.76 Q681.448 1543.08 678.3 1546.3 Q675.151 1549.52 669.92 1549.52 Q663.925 1549.52 660.753 1544.94 Q657.582 1540.33 657.582 1531.6 Q657.582 1523.41 661.471 1518.55 Q665.36 1513.66 671.911 1513.66 Q673.67 1513.66 675.452 1514.01 Q677.258 1514.36 679.202 1515.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip530)" d="M851.87 1532.44 Q848.537 1532.44 846.615 1534.22 Q844.717 1536 844.717 1539.13 Q844.717 1542.25 846.615 1544.03 Q848.537 1545.82 851.87 1545.82 Q855.203 1545.82 857.125 1544.03 Q859.046 1542.23 859.046 1539.13 Q859.046 1536 857.125 1534.22 Q855.226 1532.44 851.87 1532.44 M847.194 1530.45 Q844.185 1529.7 842.495 1527.64 Q840.828 1525.58 840.828 1522.62 Q840.828 1518.48 843.768 1516.07 Q846.731 1513.66 851.87 1513.66 Q857.032 1513.66 859.972 1516.07 Q862.912 1518.48 862.912 1522.62 Q862.912 1525.58 861.222 1527.64 Q859.555 1529.7 856.569 1530.45 Q859.949 1531.23 861.824 1533.52 Q863.722 1535.82 863.722 1539.13 Q863.722 1544.15 860.643 1546.83 Q857.588 1549.52 851.87 1549.52 Q846.152 1549.52 843.074 1546.83 Q840.018 1544.15 840.018 1539.13 Q840.018 1535.82 841.916 1533.52 Q843.815 1531.23 847.194 1530.45 M845.481 1523.06 Q845.481 1525.75 847.148 1527.25 Q848.838 1528.76 851.87 1528.76 Q854.879 1528.76 856.569 1527.25 Q858.282 1525.75 858.282 1523.06 Q858.282 1520.38 856.569 1518.87 Q854.879 1517.37 851.87 1517.37 Q848.838 1517.37 847.148 1518.87 Q845.481 1520.38 845.481 1523.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip530)" d="M1048.26 1517.37 Q1044.65 1517.37 1042.82 1520.93 Q1041.02 1524.47 1041.02 1531.6 Q1041.02 1538.71 1042.82 1542.27 Q1044.65 1545.82 1048.26 1545.82 Q1051.9 1545.82 1053.7 1542.27 Q1055.53 1538.71 1055.53 1531.6 Q1055.53 1524.47 1053.7 1520.93 Q1051.9 1517.37 1048.26 1517.37 M1048.26 1513.66 Q1054.07 1513.66 1057.13 1518.27 Q1060.21 1522.85 1060.21 1531.6 Q1060.21 1540.33 1057.13 1544.94 Q1054.07 1549.52 1048.26 1549.52 Q1042.45 1549.52 1039.38 1544.94 Q1036.32 1540.33 1036.32 1531.6 Q1036.32 1522.85 1039.38 1518.27 Q1042.45 1513.66 1048.26 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> 
 
 
 
 
 
<path clip-path="url(#clip530)" d="M62.9365 1433.67 Q59.3254 1433.67 57.4967 1437.24 Q55.6912 1440.78 55.6912 1447.91 Q55.6912 1455.01 57.4967 1458.58 Q59.3254 1462.12 62.9365 1462.12 Q66.5707 1462.12 68.3763 1458.58 Q70.205 1455.01 70.205 1447.91 Q70.205 1440.78 68.3763 1437.24 Q66.5707 1433.67 62.9365 1433.67 M62.9365 1429.97 Q68.7467 1429.97 71.8022 1434.57 Q74.8809 1439.16 74.8809 1447.91 Q74.8809 1456.63 71.8022 1461

We see that the shock $e_1$ has a persistent effect on $y_2$. It is
associated to the unit root. The new steady-state is not the original
one.

In [106]:
# explosive case
ρ = 0.3
λ = 1.02

A = [ρ 2; 0 λ]

e0_1 = [sqrt(Σ[1,1]), 0.0]
e0_2 = [0.0, sqrt(Σ[2,2])]

sim_y_1 = hcat([A^n*e0_1 for n in 0:10]...)
sim_y_2 = hcat([ A^n*e0_2 for n in 0:10 ]...)
pl1 = plot(  sim_y_1[1,:], label="\$e_2\$", title="\$y_1\$" )
plot!(pl1,sim_y_1[2,:], label="\$e_2\$")
pl2 = plot(  sim_y_2[1,:], label="\$e_2\$", title="\$y_2\$" )
plot!(pl2,sim_y_2[2,:], label="\$e_2\$", legend=false)
plot(pl1, pl2)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip620)" d="M301.307 1544.91 L317.627 1544.91 L317.627 1548.85 L295.682 1548.85 L295.682 1544.91 Q298.344 1542.16 302.928 1537.53 Q307.534 1532.88 308.715 1531.53 Q310.96 1529.01 311.84 1527.27 Q312.742 1525.51 312.742 1523.82 Q312.742 1521.07 310.798 1519.33 Q308.877 1517.6 305.775 1517.6 Q303.576 1517.6 301.122 1518.36 Q298.691 1519.13 295.914 1520.68 L295.914 1515.95 Q298.738 1514.82 301.191 1514.24 Q303.645 1513.66 305.682 1513.66 Q311.052 1513.66 314.247 1516.35 Q317.441 1519.03 317.441 1523.52 Q317.441 1525.65 316.631 1527.57 Q315.844 1529.47 313.738 1532.07 Q313.159 1532.74 310.057 1535.95 Q306.955 1539.15 301.307 1544.91 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip620)" d="M677.461 1529.7 Q674.312 1529.7 672.461 1531.86 Q670.632 1534.01 670.632 1537.76 Q670.632 1541.49 672.461 1543.66 Q674.312 1545.82 677.461 1545.82 Q680.609 1545.82 682.437 1543.66 Q684.289 1541.49 684.289 1537.76 Q684.289 1534.01 682.437 1531.86 Q680.609 1529.7 677.461 1529.7 M686.743 1515.05 L686.743 1519.31 Q684.984 1518.48 683.178 1518.04 Q681.396 1517.6 679.636 1517.6 Q675.007 1517.6 672.553 1520.72 Q670.123 1523.85 669.775 1530.17 Q671.141 1528.15 673.201 1527.09 Q675.261 1526 677.738 1526 Q682.947 1526 685.956 1529.17 Q688.988 1532.32 688.988 1537.76 Q688.988 1543.08 685.84 1546.3 Q682.692 1549.52 677.461 1549.52 Q671.465 1549.52 668.294 1544.94 Q665.123 1540.33 665.123 1531.6 Q665.123 1523.41 669.011 1518.55 Q672.9 1513.66 679.451 1513.66 Q681.21 1513.66 682.993 1514.01 Q684.798 1514.36 686.743 1515.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip620)" d="M862.256 1532.44 Q858.923 1532.44 857.001 1534.22 Q855.103 1536 855.103 1539.13 Q855.103 1542.25 857.001 1544.03 Q858.923 1545.82 862.256 1545.82 Q865.589 1545.82 867.511 1544.03 Q869.432 1542.23 869.432 1539.13 Q869.432 1536 867.511 1534.22 Q865.612 1532.44 862.256 1532.44 M857.58 1530.45 Q854.571 1529.7 852.881 1527.64 Q851.214 1525.58 851.214 1522.62 Q851.214 1518.48 854.154 1516.07 Q857.117 1513.66 862.256 1513.66 Q867.418 1513.66 870.358 1516.07 Q873.298 1518.48 873.298 1522.62 Q873.298 1525.58 871.608 1527.64 Q869.941 1529.7 866.955 1530.45 Q870.335 1531.23 872.21 1533.52 Q874.108 1535.82 874.108 1539.13 Q874.108 1544.15 871.029 1546.83 Q867.974 1549.52 862.256 1549.52 Q856.538 1549.52 853.46 1546.83 Q850.404 1544.15 850.404 1539.13 Q850.404 1535.82 852.302 1533.52 Q854.2 1531.23 857.58 1530.45 M855.867 1523.06 Q855.867 1525.75 857.534 1527.25 Q859.224 1528.76 862.256 1528.76 Q865.265 1528.76 866.955 1527.25 Q868.668 1525.75 868.668 1523.06 Q868.668 1520.38 866.955 1518.87 Q865.265 1517.37 862.256 1517.37 Q859.224 1517.37 857.534 1518.87 Q855.867 1520.38 855.867 1523.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip620)" d="M1061.5 1517.37 Q1057.88 1517.37 1056.06 1520.93 Q1054.25 1524.47 1054.25 1531.6 Q1054.25 1538.71 1056.06 1542.27 Q1057.88 1545.82 1061.5 1545.82 Q1065.13 1545.82 1066.94 1542.27 Q1068.76 1538.71 1068.76 1531.6 Q1068.76 1524.47 1066.94 1520.93 Q1065.13 1517.37 1061.5 1517.37 M1061.5 1513.66 Q1067.31 1513.66 1070.36 1518.27 Q1073.44 1522.85 1073.44 1531.6 Q1073.44 1540.33 1070.36 1544.94 Q1067.31 1549.52 1061.5 1549.52 Q1055.69 1549.52 1052.61 1544.94 Q1049.55 1540.33 1049.55 1531.6 Q1049.55 1522.85 1052.61 1518.27 Q1055.69 1513.66 1061.5 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> 
 
 
 
 
 
<path clip-path="url(#clip620)" d="M62.9365 1433.67 Q59.3254 1433.67 57.4967 1437.24 Q55.6912 1440.78 55.6912 1447.91 Q55.6912 1455.01 57.4967 1458.58 Q59.3254 1462.12 62.9365 1462.12 Q66.5707 1462.12 68.3763 1458.58 Q70.205 1455.01 70.205 1447.91 Q70.205 1440.78 68.3763 1437.24 Q66.5707 1433.67 62.9365 1433.67 M62.9365 1429.97 Q68.7467 1429.97 71.8022 1434.57 Q74.8809 1439.16 74.8809 1447.91 Q74.8809 1456.63 71.8022

Now the variable $y_2$ diverges. Note that $y_1$ does not diverge
because of the specific initial shock (colinear to \[1,0\]).

**Import the Distributions package. Use `MvNormal` to compute draws from
a multivariate distribution with covariance matrix $\Sigma$**

In [110]:
# we need the distributions package to compute mvnormal
# import Pkg; Pkg.add("Distributions")

In [111]:
using Distributions

# MvNormal
# check the doc

In [112]:
dis = MvNormal(Σ)
rand(dis)

2-element Vector{Float64}:
 -0.055367726741675345
 -0.13620922040042954

In [113]:
# we can plot the distribution of $\epsilon$
random_points = [rand(dis) for i=1:1000]
pl = scatter([e[1] for e in random_points], [e[2] for e in random_points])


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip710)" d="M252.861 1517.37 Q249.25 1517.37 247.421 1520.93 Q245.616 1524.47 245.616 1531.6 Q245.616 1538.71 247.421 1542.27 Q249.25 1545.82 252.861 1545.82 Q256.495 1545.82 258.301 1542.27 Q260.13 1538.71 260.13 1531.6 Q260.13 1524.47 258.301 1520.93 Q256.495 1517.37 252.861 1517.37 M252.861 1513.66 Q258.671 1513.66 261.727 1518.27 Q264.806 1522.85 264.806 1531.6 Q264.806 1540.33 261.727 1544.94 Q258.671 1549.52 252.861 1549.52 Q247.051 1549.52 243.972 1544.94 Q240.917 1540.33 240.917 1531.6 Q240.917 1522.85 243.972 1518.27 Q247.051 1513.66 252.861 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip710)" d="M318.301 1514.29 L336.657 1514.29 L336.657 1518.22 L322.583 1518.22 L322.583 1526.7 Q323.602 1526.35 324.62 1526.19 Q325.639 1526 326.657 1526 Q332.444 1526 335.824 1529.17 Q339.203 1532.34 339.203 1537.76 Q339.203 1543.34 335.731 1546.44 Q332.259 1549.52 325.94 1549.52 Q323.764 1549.52 321.495 1549.15 Q319.25 1548.78 316.842 1548.04 L316.842 1543.34 Q318.926 1544.47 321.148 1545.03 Q323.37 1545.58 325.847 1545.58 Q329.852 1545.58 332.19 1543.48 Q334.527 1541.37 334.527 1537.76 Q334.527 1534.15 332.19 1532.04 Q329.852 1529.94 325.847 1529.94 Q323.972 1529.94 322.097 1530.35 Q320.245 1530.77 318.301 1531.65 L318.301 1514.29 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip710)" d="M624.264 1517.37 Q620.653 1517.37 618.824 1520.93 Q617.018 1524.47 617.018 1531.6 Q617.018 1538.71 618.824 1542.27 Q620.653 1545.82 624.264 1545.82 Q627.898 1545.82 629.703 1542.27 Q631.532 1538.71 631.532 1531.6 Q631.532 1524.47 629.703 1520.93 Q627.898 1517.37 624.264 1517.37 M624.264 1513.66 Q630.074 1513.66 633.129 1518.27 Q636.208 1522.85 636.208 1531.6 Q636.208 1540.33 633.129 1544.94 Q630.074 1549.52 624.264 1549.52 Q618.454 1549.52 615.375 1544.94 Q612.319 1540.33 612.319 1531.6 Q612.319 1522.85 615.375 1518.27 Q618.454 1513.66 624.264 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip710)" d="M659.541 1514.29 L677.898 1514.29 L677.898 1518.22 L663.824 1518.22 L663.824 1526.7 Q664.842 1526.35 665.861 1526.19 Q666.879 1526 667.898 1526 Q673.685 1526 677.064 1529.17 Q680.444 1532.34 680.444 1537.76 Q680.444 1543.34 676.972 1546.44 Q673.5 1549.52 667.18 1549.52 Q665.004 1549.52 662.736 1549.15 Q660.49 1548.78 658.083 1548.04 L658.083 1543.34 Q660.166 1544.47 662.388 1545.03 Q664.611 1545.58 667.088 1545.58 Q671.092 1545.58 673.43 1543.48 Q675.768 1541.37 675.768 1537.76 Q675.768 1534.15 673.43 1532.04 Q671.092 1529.94 667.088 1529.94 Q665.213 1529.94 663.338 1530.35 Q661.486 1530.77 659.541 1531.65 L659.541 1514.29 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip710)" d="M699.657 1517.37 Q696.046 1517.37 694.217 1520.93 Q692.411 1524.47 692.411 1531.6 Q692.411 1538.71 694.217 1542.27 Q696.046 1545.82 699.657 1545.82 Q703.291 1545.82 705.097 1542.27 Q706.925 1538.71 706.925 1531.6 Q706.925 1524.47 705.097 1520.93 Q703.291 1517.37 699.657 1517.37 M699.657 1513.66 Q705.467 1513.66 708.522 1518.27 Q711.601 1522.85 711.601 1531.6 Q711.601 1540.33 708.522 1544.94 Q705.467 1549.52 699.657 1549.52 Q693.847 1549.52 690.768 1544.94 Q687.712 1540.33 687.712 1531.6 Q687.712 1522.85 690.768 1518.27 Q693.847 1513.66 699.657 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip710)" d="M996.661 1517.37 Q993.05 1517.37 991.222 1520.93 Q989.416 1524.47 989.416 1531.6 Q989.416 1538.71 991.222 1542.27 Q993.05 1545.82 996.661 1545.82 Q1000.3 1545.82 1002.1 1542.27 Q1003.93 1538.71 1003.93 1531.6 Q1003.93 1524.47 1002.1 1520.93 Q1000.3 1517.37 996.661 1517.37 M996.661 1513.66 Q1002.47 1513.66 1005.53 1518.27 Q1008.61 1522.85 1008.61 1531.6 Q1008.61 1540.33 1005.53 1544.94 Q1002.47 1549.52 996.661 1549.52 Q990.851 1549.52 987.773 1544.94 

In [120]:
# even better, with the StatsPlots Library
# import Pkg; Pkg.add("StatsPlots")

In [121]:
using StatsPlots
random_points = [rand(dis) for i=1:1000]
pl = scatter([e[1] for e in random_points], [e[2] for e in random_points], label="e", xlabel="\$e_1\$", ylabel="\$e_2\$")
covellipse!([0,0], Σ, n_std=2, aspect_ratio=1, label="cov")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip890)" d="M472.486 1454.1 Q468.875 1454.1 467.046 1457.66 Q465.241 1461.2 465.241 1468.33 Q465.241 1475.44 467.046 1479.01 Q468.875 1482.55 472.486 1482.55 Q476.12 1482.55 477.926 1479.01 Q479.755 1475.44 479.755 1468.33 Q479.755 1461.2 477.926 1457.66 Q476.12 1454.1 472.486 1454.1 M472.486 1450.39 Q478.296 1450.39 481.352 1455 Q484.431 1459.58 484.431 1468.33 Q484.431 1477.06 481.352 1481.67 Q478.296 1486.25 472.486 1486.25 Q466.676 1486.25 463.597 1481.67 Q460.542 1477.06 460.542 1468.33 Q460.542 1459.58 463.597 1455 Q466.676 1450.39 472.486 1450.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip890)" d="M537.926 1451.02 L556.282 1451.02 L556.282 1454.96 L542.208 1454.96 L542.208 1463.43 Q543.226 1463.08 544.245 1462.92 Q545.264 1462.73 546.282 1462.73 Q552.069 1462.73 555.449 1465.9 Q558.828 1469.08 558.828 1474.49 Q558.828 1480.07 555.356 1483.17 Q551.884 1486.25 545.564 1486.25 Q543.389 1486.25 541.12 1485.88 Q538.875 1485.51 536.467 1484.77 L536.467 1480.07 Q538.551 1481.2 540.773 1481.76 Q542.995 1482.32 545.472 1482.32 Q549.476 1482.32 551.814 1480.21 Q554.152 1478.1 554.152 1474.49 Q554.152 1470.88 551.814 1468.77 Q549.476 1466.67 545.472 1466.67 Q543.597 1466.67 541.722 1467.08 Q539.87 1467.5 537.926 1468.38 L537.926 1451.02 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip890)" d="M807.239 1454.1 Q803.628 1454.1 801.799 1457.66 Q799.994 1461.2 799.994 1468.33 Q799.994 1475.44 801.799 1479.01 Q803.628 1482.55 807.239 1482.55 Q810.873 1482.55 812.679 1479.01 Q814.508 1475.44 814.508 1468.33 Q814.508 1461.2 812.679 1457.66 Q810.873 1454.1 807.239 1454.1 M807.239 1450.39 Q813.049 1450.39 816.105 1455 Q819.183 1459.58 819.183 1468.33 Q819.183 1477.06 816.105 1481.67 Q813.049 1486.25 807.239 1486.25 Q801.429 1486.25 798.35 1481.67 Q795.295 1477.06 795.295 1468.33 Q795.295 1459.58 798.35 1455 Q801.429 1450.39 807.239 1450.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip890)" d="M842.517 1451.02 L860.873 1451.02 L860.873 1454.96 L846.799 1454.96 L846.799 1463.43 Q847.818 1463.08 848.836 1462.92 Q849.855 1462.73 850.873 1462.73 Q856.66 1462.73 860.04 1465.9 Q863.419 1469.08 863.419 1474.49 Q863.419 1480.07 859.947 1483.17 Q856.475 1486.25 850.156 1486.25 Q847.98 1486.25 845.711 1485.88 Q843.466 1485.51 841.058 1484.77 L841.058 1480.07 Q843.142 1481.2 845.364 1481.76 Q847.586 1482.32 850.063 1482.32 Q854.068 1482.32 856.406 1480.21 Q858.743 1478.1 858.743 1474.49 Q858.743 1470.88 856.406 1468.77 Q854.068 1466.67 850.063 1466.67 Q848.188 1466.67 846.313 1467.08 Q844.461 1467.5 842.517 1468.38 L842.517 1451.02 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip890)" d="M882.632 1454.1 Q879.021 1454.1 877.192 1457.66 Q875.387 1461.2 875.387 1468.33 Q875.387 1475.44 877.192 1479.01 Q879.021 1482.55 882.632 1482.55 Q886.266 1482.55 888.072 1479.01 Q889.901 1475.44 889.901 1468.33 Q889.901 1461.2 888.072 1457.66 Q886.266 1454.1 882.632 1454.1 M882.632 1450.39 Q888.442 1450.39 891.498 1455 Q894.577 1459.58 894.577 1468.33 Q894.577 1477.06 891.498 1481.67 Q888.442 1486.25 882.632 1486.25 Q876.822 1486.25 873.743 1481.67 Q870.688 1477.06 870.688 1468.33 Q870.688 1459.58 873.743 1455 Q876.822 1450.39 882.632 1450.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip890)" d="M1142.99 1454.1 Q1139.38 1454.1 1137.55 1457.66 Q1135.74 1461.2 1135.74 1468.33 Q1135.74 1475.44 1137.55 1479.01 Q1139.38 1482.55 1142.99 1482.55 Q1146.62 1482.55 1148.43 1479.01 Q1150.26 1475.44 1150.26 1468.33 Q1150.26 1461.2 1148.43 1457.66 Q1146.62 1454.1 1142.99 1454.1 M1142.99 1450.39 Q1148.8 1450.39 1151.85 1455 Q1154.93 1459.58 1154.93 1468.33 Q1154.93 1477.06 1151.85 1481.67 Q1148.8 1486.25 1142.99 1486.25 Q1137.18 1486.25 1134.1 1481.67 Q1131.04 14

**Perform a stochastic simulation over 20 periods starting with a one
standard-deviation in $e_2$.**

In [122]:
# return to old value of A
ρ = 0.3
λ = 0.5

A = [ρ 2; 0 λ]

2×2 Matrix{Float64}:
 0.3  2.0
 0.0  0.5

In [124]:
function simulate(A,B,Σ,e0=zeros(2); T=20)
    
    # initialize distribution object
    dis = MvNormal(Σ)
    
    # create vector to hold the simulation
    sim = [B*e0]

    for t=1:T

        e1 = rand(dis)

        y0 = sim[end] # last value
        y1 = A*y0 + B*e1

        push!(sim, y1)


    end

    return hcat(sim...)
end

simulate (generic function with 2 methods)

In [125]:
sim = simulate(A,B,Σ,e0_2)

2×21 Matrix{Float64}:
 0.0  0.392371    0.374782  -0.101664   …  0.42125   0.472957   0.168838
 0.1  0.0844052  -0.015747  -0.0961442     0.172038  0.133797  -0.184264

In [126]:
plot(
    plot(sim[1,:], title="\$y_1\$" ),
    plot(sim[2,:], title="\$y_2\$" )
)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip980)" d="M392.826 1514.29 L411.183 1514.29 L411.183 1518.22 L397.109 1518.22 L397.109 1526.7 Q398.127 1526.35 399.146 1526.19 Q400.164 1526 401.183 1526 Q406.97 1526 410.349 1529.17 Q413.729 1532.34 413.729 1537.76 Q413.729 1543.34 410.257 1546.44 Q406.784 1549.52 400.465 1549.52 Q398.289 1549.52 396.021 1549.15 Q393.775 1548.78 391.368 1548.04 L391.368 1543.34 Q393.451 1544.47 395.673 1545.03 Q397.896 1545.58 400.372 1545.58 Q404.377 1545.58 406.715 1543.48 Q409.053 1541.37 409.053 1537.76 Q409.053 1534.15 406.715 1532.04 Q404.377 1529.94 400.372 1529.94 Q398.497 1529.94 396.622 1530.35 Q394.771 1530.77 392.826 1531.65 L392.826 1514.29 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip980)" d="M642.812 1517.37 Q639.201 1517.37 637.372 1520.93 Q635.566 1524.47 635.566 1531.6 Q635.566 1538.71 637.372 1542.27 Q639.201 1545.82 642.812 1545.82 Q646.446 1545.82 648.251 1542.27 Q650.08 1538.71 650.08 1531.6 Q650.08 1524.47 648.251 1520.93 Q646.446 1517.37 642.812 1517.37 M642.812 1513.66 Q648.622 1513.66 651.677 1518.27 Q654.756 1522.85 654.756 1531.6 Q654.756 1540.33 651.677 1544.94 Q648.622 1549.52 642.812 1549.52 Q637.002 1549.52 633.923 1544.94 Q630.867 1540.33 630.867 1531.6 Q630.867 1522.85 633.923 1518.27 Q637.002 1513.66 642.812 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip980)" d="M859.58 1514.29 L877.936 1514.29 L877.936 1518.22 L863.862 1518.22 L863.862 1526.7 Q864.881 1526.35 865.899 1526.19 Q866.918 1526 867.936 1526 Q873.723 1526 877.103 1529.17 Q880.483 1532.34 880.483 1537.76 Q880.483 1543.34 877.01 1546.44 Q873.538 1549.52 867.219 1549.52 Q865.043 1549.52 862.774 1549.15 Q860.529 1548.78 858.122 1548.04 L858.122 1543.34 Q860.205 1544.47 862.427 1545.03 Q864.649 1545.58 867.126 1545.58 Q871.131 1545.58 873.469 1543.48 Q875.807 1541.37 875.807 1537.76 Q875.807 1534.15 873.469 1532.04 Q871.131 1529.94 867.126 1529.94 Q865.251 1529.94 863.376 1530.35 Q861.524 1530.77 859.58 1531.65 L859.58 1514.29 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip980)" d="M1059.99 1544.91 L1076.31 1544.91 L1076.31 1548.85 L1054.37 1548.85 L1054.37 1544.91 Q1057.03 1542.16 1061.61 1537.53 Q1066.22 1532.88 1067.4 1531.53 Q1069.65 1529.01 1070.53 1527.27 Q1071.43 1525.51 1071.43 1523.82 Q1071.43 1521.07 1069.48 1519.33 Q1067.56 1517.6 1064.46 1517.6 Q1062.26 1517.6 1059.81 1518.36 Q1057.38 1519.13 1054.6 1520.68 L1054.6 1515.95 Q1057.42 1514.82 1059.88 1514.24 Q1062.33 1513.66 1064.37 1513.66 Q1069.74 1513.66 1072.93 1516.35 Q1076.13 1519.03 1076.13 1523.52 Q1076.13 1525.65 1075.32 1527.57 Q1074.53 1529.47 1072.42 1532.07 Q1071.85 1532.74 1068.74 1535.95 Q1065.64 1539.15 1059.99 1544.91 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip980)" d="M1096.13 1517.37 Q1092.52 1517.37 1090.69 1520.93 Q1088.88 1524.47 1088.88 1531.6 Q1088.88 1538.71 1090.69 1542.27 Q1092.52 1545.82 1096.13 1545.82 Q1099.76 1545.82 1101.57 1542.27 Q1103.4 1538.71 1103.4 1531.6 Q1103.4 1524.47 1101.57 1520.93 Q1099.76 1517.37 1096.13 1517.37 M1096.13 1513.66 Q1101.94 1513.66 1104.99 1518.27 Q1108.07 1522.85 1108.07 1531.6 Q1108.07 1540.33 1104.99 1544.94 Q1101.94 1549.52 1096.13 1549.52 Q1090.32 1549.52 1087.24 1544.94 Q1084.18 1540.33 1084.18 1531.6 Q1084.18 1522.85 1087.24 1518.27 Q1090.32 1513.66 1096.13 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> 
 
 
 
 
 
 
 <path clip-path="url(#clip980)" d="M100.76 1353.54 Q97.1493 1353.54 95.3206 1357.11 Q93.515 1360.65 93.515 1367.78 Q93.515 1374.89 95.3206 1378.45 Q97.1493 1381.99 100.76 1381.99 Q104.395 1381.99 106.2 1378.45 Q108.029 1374.89 108.029 1367.78 Q108.029 1360.65 106.2 1357.11 Q104.395 1353.54 100.76 1353.54 M100.76 1349.84 Q106.571 1349.84 109.626 1354.45 Q112.705 1359.03 112.705 1367.78 Q112.705 1376.51 109.626 13

Much harder to intepret results from a single simulation…

**Perform K=500 stochastic simulations over 20 periods starting with a
one standard-deviation in $e_2$. Plot the result.**

In [127]:
K = 500
sims = [simulate(A,B,Σ,e0_2) for n=1:K] 

500-element Vector{Matrix{Float64}}:
 [0.0 0.3519136419682234 … -0.13632256187189307 0.28734699004199543; 0.1 0.03458950910034711 … 0.05590879127288487 0.1821378027563172]
 [0.0 0.18735118271396525 … -0.5792223496408389 -0.12954015040579497; 0.1 -0.017113568280008512 … 0.06610668517404303 0.034768318939232185]
 [0.0 -0.26355803168343 … 0.13331606138155416 0.10605379996605355; 0.1 -0.08203172271058749 … 0.08789623820459265 0.04302552416068846]
 [0.0 0.447924703915066 … -0.6840511756042715 -0.5087494379321347; 0.1 0.13240167512832168 … -0.13923613251848604 -0.30739802372828207]
 [0.0 0.2864585646636234 … -0.8972892768061322 -0.32525236081256703; 0.1 0.052085969055819484 … -0.009248985478192695 0.19809006901765033]
 [0.0 0.3176852256968753 … -0.07299075149807696 -0.1994033938565344; 0.1 0.04893276414828989 … -0.029399256319346128 -0.17523773567963405]
 [0.0 -0.20515053466386868 … 0.11551566975384928 0.24349840611342544; 0.1 0.10551318621350193 … -0.06835216203436546 0.1977318992358082]
 [

In [128]:
pl1 = plot()
for sim in sims
    plot!(pl1, sim[1,:], title="\$y_1\$", legend=false, color="red", alpha=0.01)
end

# add average
average_1 = [ mean( [sim[1,t] for sim in sims] ) for t=1:size(sims[1],2)]
std_1 = [ std( [sim[1,t] for sim in sims] ) for t=1:size(sims[1],2)]

plot!(pl1, average_1, color="blue")
plot!(pl1, average_1-std_1, color="blue", linestyle=:dash)
plot!(pl1, average_1+std_1, color="blue", linestyle=:dash)

pl2 = plot()
for sim in sims
    plot!(pl2, sim[2,:], title="\$y_2\$", legend=false , color="red", alpha=0.01)
end

# add average
average_2 = [ mean( [sim[2,t] for sim in sims] ) for t=1:size(sims[1],2)]
std_2 = [ std( [sim[2,t] for sim in sims] ) for t=1:size(sims[1],2)]

plot!(pl2, average_2, color="blue")
plot!(pl2, average_2-std_2, color="blue", linestyle=:dash)

plot!(pl2, average_2+std_2, color="blue", linestyle=:dash)

plot(pl1, pl2)


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip070)" d="M392.207 1514.29 L410.563 1514.29 L410.563 1518.22 L396.489 1518.22 L396.489 1526.7 Q397.508 1526.35 398.526 1526.19 Q399.545 1526 400.563 1526 Q406.35 1526 409.73 1529.17 Q413.11 1532.34 413.11 1537.76 Q413.11 1543.34 409.637 1546.44 Q406.165 1549.52 399.846 1549.52 Q397.67 1549.52 395.401 1549.15 Q393.156 1548.78 390.749 1548.04 L390.749 1543.34 Q392.832 1544.47 395.054 1545.03 Q397.276 1545.58 399.753 1545.58 Q403.758 1545.58 406.096 1543.48 Q408.434 1541.37 408.434 1537.76 Q408.434 1534.15 406.096 1532.04 Q403.758 1529.94 399.753 1529.94 Q397.878 1529.94 396.003 1530.35 Q394.151 1530.77 392.207 1531.65 L392.207 1514.29 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip070)" d="M642.048 1517.37 Q638.437 1517.37 636.608 1520.93 Q634.802 1524.47 634.802 1531.6 Q634.802 1538.71 636.608 1542.27 Q638.437 1545.82 642.048 1545.82 Q645.682 1545.82 647.488 1542.27 Q649.316 1538.71 649.316 1531.6 Q649.316 1524.47 647.488 1520.93 Q645.682 1517.37 642.048 1517.37 M642.048 1513.66 Q647.858 1513.66 650.914 1518.27 Q653.992 1522.85 653.992 1531.6 Q653.992 1540.33 650.914 1544.94 Q647.858 1549.52 642.048 1549.52 Q636.238 1549.52 633.159 1544.94 Q630.103 1540.33 630.103 1531.6 Q630.103 1522.85 633.159 1518.27 Q636.238 1513.66 642.048 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip070)" d="M858.671 1514.29 L877.028 1514.29 L877.028 1518.22 L862.954 1518.22 L862.954 1526.7 Q863.972 1526.35 864.991 1526.19 Q866.009 1526 867.028 1526 Q872.815 1526 876.194 1529.17 Q879.574 1532.34 879.574 1537.76 Q879.574 1543.34 876.102 1546.44 Q872.63 1549.52 866.31 1549.52 Q864.134 1549.52 861.866 1549.15 Q859.62 1548.78 857.213 1548.04 L857.213 1543.34 Q859.296 1544.47 861.518 1545.03 Q863.741 1545.58 866.218 1545.58 Q870.222 1545.58 872.56 1543.48 Q874.898 1541.37 874.898 1537.76 Q874.898 1534.15 872.56 1532.04 Q870.222 1529.94 866.218 1529.94 Q864.343 1529.94 862.468 1530.35 Q860.616 1530.77 858.671 1531.65 L858.671 1514.29 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip070)" d="M1058.94 1544.91 L1075.26 1544.91 L1075.26 1548.85 L1053.32 1548.85 L1053.32 1544.91 Q1055.98 1542.16 1060.56 1537.53 Q1065.17 1532.88 1066.35 1531.53 Q1068.59 1529.01 1069.47 1527.27 Q1070.38 1525.51 1070.38 1523.82 Q1070.38 1521.07 1068.43 1519.33 Q1066.51 1517.6 1063.41 1517.6 Q1061.21 1517.6 1058.76 1518.36 Q1056.32 1519.13 1053.55 1520.68 L1053.55 1515.95 Q1056.37 1514.82 1058.82 1514.24 Q1061.28 1513.66 1063.32 1513.66 Q1068.69 1513.66 1071.88 1516.35 Q1075.07 1519.03 1075.07 1523.52 Q1075.07 1525.65 1074.26 1527.57 Q1073.48 1529.47 1071.37 1532.07 Q1070.79 1532.74 1067.69 1535.95 Q1064.59 1539.15 1058.94 1544.91 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip070)" d="M1095.07 1517.37 Q1091.46 1517.37 1089.63 1520.93 Q1087.83 1524.47 1087.83 1531.6 Q1087.83 1538.71 1089.63 1542.27 Q1091.46 1545.82 1095.07 1545.82 Q1098.71 1545.82 1100.51 1542.27 Q1102.34 1538.71 1102.34 1531.6 Q1102.34 1524.47 1100.51 1520.93 Q1098.71 1517.37 1095.07 1517.37 M1095.07 1513.66 Q1100.88 1513.66 1103.94 1518.27 Q1107.02 1522.85 1107.02 1531.6 Q1107.02 1540.33 1103.94 1544.94 Q1100.88 1549.52 1095.07 1549.52 Q1089.26 1549.52 1086.19 1544.94 Q1083.13 1540.33 1083.13 1531.6 Q1083.13 1522.85 1086.19 1518.27 Q1089.26 1513.66 1095.07 1513.66 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> 
 
 
 
 
 
 
 <path clip-path="url(#clip070)" d="M145.992 1271.75 Q142.381 1271.75 140.552 1275.32 Q138.746 1278.86 138.746 1285.99 Q138.746 1293.1 140.552 1296.66 Q142.381 1300.2 145.992 1300.2 Q149.626 1300.2 151.431 1296.66 Q153.26 1293.1 153.26 1285.99 Q153.26 1278.86 151.431 1275.32 Q149.626 1271.75 145.992 1271.75 M145.992 1268.05 Q151.802 1268.05 154.857 1272.66 Q157.936 1277.24 157.936 1285.99 Q157.936 1294.72 154.

We observe that:

1.  the *expected* response is similar to the determinstic irf we
    computed before
2.  volatility makes predictions hard..
3.  it looks like the unconditional volatility converges after a few
    periods

**Ergodic Distribution.**

It can be shown that the ergodic distribution of a VAR1 is a
multivariate normal law, with covariance matrix $\Omega$.

This matrix is a solution to the equation
$\Omega = A \Omega A' + B \Sigma B'$.

A simple algorithm to find it consist in applying the recurrence
$\Omega_n = A \Omega_{n-1} A' + B \Sigma B'$ until convergence, starting
with $\Omega_0 =0$.

Implement this algorithm.

In [129]:
function ergodic_steady_state(A,B,Σ; N=1000, tol_η=1e-8)
    Ω0 = Σ*0
    for n = 1:N
        Ω = A*Ω0*A'+B*Σ*B'
        η = maximum( abs.( Ω - Ω0) )
        if η<tol_η
            return Ω
        end
        Ω0 = Ω
    end
    error("No convergence")
end


ergodic_steady_state (generic function with 1 method)

**Compare the result with the empirical ergodic distribution obtained
from the simulations**

In [130]:
random_final_points = [sim[:,end] for sim in sims]

500-element Vector{Vector{Float64}}:
 [0.28734699004199543, 0.1821378027563172]
 [-0.12954015040579497, 0.034768318939232185]
 [0.10605379996605355, 0.04302552416068846]
 [-0.5087494379321347, -0.30739802372828207]
 [-0.32525236081256703, 0.19809006901765033]
 [-0.1994033938565344, -0.17523773567963405]
 [0.24349840611342544, 0.1977318992358082]
 [-0.5004115801583995, -0.20431976135074786]
 [-0.09365511537178871, -0.02405222464014385]
 [0.22238420401920062, 0.15540654408684915]
 ⋮
 [0.35324198956855907, -0.052414251103087166]
 [-0.3980090459422957, -0.02266753697793905]
 [-0.07992915762258111, 0.16166607816954648]
 [-0.0019249994388082642, 0.10462559642266155]
 [-0.21584697092718536, -0.19127247705898093]
 [1.072163516270816, 0.24147810520943158]
 [0.2834922315575247, 0.2046794210651945]
 [-0.2854383438166833, -0.061626044462775316]
 [-0.3585049280601489, -0.02995515122129525]

In [131]:
Ω = ergodic_steady_state(A,B,Σ)

2×2 Matrix{Float64}:
 0.141995   0.0215686
 0.0215686  0.0133333

In [132]:
# empirical covariance
cov( random_final_points)
# very close to theoretical one

2×2 Matrix{Float64}:
 0.138121   0.0217592
 0.0217592  0.0133982

In [133]:

# graphical representation
using StatsPlots

pl = scatter([e[1] for e in random_final_points], [e[2] for e in random_final_points], label="e", xlabel="\$e_1\$", ylabel="\$e_2\$", alpha=0.2)
covellipse!([0,0], Ω, n_std=2, aspect_ratio=1, label="cov")
# let's add the expected path
plot!(pl, average_1, average_2, color="black")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip160)" d="M385.222 1454.1 Q381.611 1454.1 379.782 1457.66 Q377.976 1461.2 377.976 1468.33 Q377.976 1475.44 379.782 1479.01 Q381.611 1482.55 385.222 1482.55 Q388.856 1482.55 390.661 1479.01 Q392.49 1475.44 392.49 1468.33 Q392.49 1461.2 390.661 1457.66 Q388.856 1454.1 385.222 1454.1 M385.222 1450.39 Q391.032 1450.39 394.087 1455 Q397.166 1459.58 397.166 1468.33 Q397.166 1477.06 394.087 1481.67 Q391.032 1486.25 385.222 1486.25 Q379.412 1486.25 376.333 1481.67 Q373.277 1477.06 373.277 1468.33 Q373.277 1459.58 376.333 1455 Q379.412 1450.39 385.222 1450.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip160)" d="M780.498 1454.1 Q776.887 1454.1 775.058 1457.66 Q773.253 1461.2 773.253 1468.33 Q773.253 1475.44 775.058 1479.01 Q776.887 1482.55 780.498 1482.55 Q784.132 1482.55 785.938 1479.01 Q787.767 1475.44 787.767 1468.33 Q787.767 1461.2 785.938 1457.66 Q784.132 1454.1 780.498 1454.1 M780.498 1450.39 Q786.308 1450.39 789.364 1455 Q792.442 1459.58 792.442 1468.33 Q792.442 1477.06 789.364 1481.67 Q786.308 1486.25 780.498 1486.25 Q774.688 1486.25 771.609 1481.67 Q768.554 1477.06 768.554 1468.33 Q768.554 1459.58 771.609 1455 Q774.688 1450.39 780.498 1450.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip160)" d="M815.776 1451.02 L834.132 1451.02 L834.132 1454.96 L820.058 1454.96 L820.058 1463.43 Q821.077 1463.08 822.095 1462.92 Q823.114 1462.73 824.132 1462.73 Q829.919 1462.73 833.299 1465.9 Q836.678 1469.08 836.678 1474.49 Q836.678 1480.07 833.206 1483.17 Q829.734 1486.25 823.415 1486.25 Q821.239 1486.25 818.97 1485.88 Q816.725 1485.51 814.317 1484.77 L814.317 1480.07 Q816.401 1481.2 818.623 1481.76 Q820.845 1482.32 823.322 1482.32 Q827.327 1482.32 829.664 1480.21 Q832.002 1478.1 832.002 1474.49 Q832.002 1470.88 829.664 1468.77 Q827.327 1466.67 823.322 1466.67 Q821.447 1466.67 819.572 1467.08 Q817.72 1467.5 815.776 1468.38 L815.776 1451.02 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip160)" d="M1201.1 1454.1 Q1197.49 1454.1 1195.66 1457.66 Q1193.85 1461.2 1193.85 1468.33 Q1193.85 1475.44 1195.66 1479.01 Q1197.49 1482.55 1201.1 1482.55 Q1204.73 1482.55 1206.54 1479.01 Q1208.37 1475.44 1208.37 1468.33 Q1208.37 1461.2 1206.54 1457.66 Q1204.73 1454.1 1201.1 1454.1 M1201.1 1450.39 Q1206.91 1450.39 1209.96 1455 Q1213.04 1459.58 1213.04 1468.33 Q1213.04 1477.06 1209.96 1481.67 Q1206.91 1486.25 1201.1 1486.25 Q1195.29 1486.25 1192.21 1481.67 Q1189.15 1477.06 1189.15 1468.33 Q1189.15 1459.58 1192.21 1455 Q1195.29 1450.39 1201.1 1450.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip160)" d="M1246.33 1454.1 Q1242.72 1454.1 1240.89 1457.66 Q1239.08 1461.2 1239.08 1468.33 Q1239.08 1475.44 1240.89 1479.01 Q1242.72 1482.55 1246.33 1482.55 Q1249.96 1482.55 1251.77 1479.01 Q1253.6 1475.44 1253.6 1468.33 Q1253.6 1461.2 1251.77 1457.66 Q1249.96 1454.1 1246.33 1454.1 M1246.33 1450.39 Q1252.14 1450.39 1255.2 1455 Q1258.27 1459.58 1258.27 1468.33 Q1258.27 1477.06 1255.2 1481.67 Q1252.14 1486.25 1246.33 1486.25 Q1240.52 1486.25 1237.44 1481.67 Q1234.39 1477.06 1234.39 1468.33 Q1234.39 1459.58 1237.44 1455 Q1240.52 1450.39 1246.33 1450.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip160)" d="M1641.61 1454.1 Q1638 1454.1 1636.17 1457.66 Q1634.36 1461.2 1634.36 1468.33 Q1634.36 1475.44 1636.17 1479.01 Q1638 1482.55 1641.61 1482.55 Q1645.24 1482.55 1647.05 1479.01 Q1648.87 1475.44 1648.87 1468.33 Q1648.87 1461.2 1647.05 1457.66 Q1645.24 1454.1 1641.61 1454.1 M1641.61 1450.39 Q1647.42 1450.39 1650.47 1455 Q1653.55 1459.58 1653.55 1468.33 Q1653.55 1477.06 1650.47 1481.67 Q1647.42 1486.25 1641.61 1486.25 Q1635.8 1486.25 1632.72 1481.67 Q1629.66 1477.06 1629.66 1468.33 Q1629.66 1459.58 1632.72 1455 Q1635.8 1450.39 1641.61 1450.39 Z" fill="#000000" fil